## Results analysis

In this jupyter notebook I will try to examine why models are making mistakes during classification. To achieve that I have to use code from benchmark.py, select dataset, train model and examine what went wrong. I have used LIME algorithm (**eli5** and **lime** module) to visualize weights assigned to every word and every target class.

In [1]:
%%javascript
IPython.OutputArea.prototype._should_scroll = function(lines) {
    return false;
}

<IPython.core.display.Javascript object>

In [33]:
import argparse
import numpy as np
import pandas as pd
import time
from sklearn.model_selection import KFold
from sklearn.model_selection import train_test_split

from load_dataset import load_bbc_dataset
from load_dataset import load_news_groups_dataset
from load_dataset import load_yahoo_answers_dataset
from load_dataset import load_ohsumed_dataset
from load_dataset import load_reuters_dataset
from models.tfidf_model import TfIdfModel
from models.doc2vec_model import Doc2VecDBOWModel, Doc2VecDMModel
from models.lda_model import LDAModel
from models.lsa_model import LSAModel
from models.han_model import HANModel
from models.sif_model import SIFModel
from models.cbow_model import CBOWModel

import logging
import multiprocessing
cores = multiprocessing.cpu_count() - 1

parser =  argparse.ArgumentParser(
    description="Benchmark for documents embedding methods")

parser.add_argument("-d",
    "--dataset_path",
    dest="dataset_path",
    required=True,
    help="Path to dataset")

parser.add_argument("-m",
    "--models_path",
    dest="models_path",
    required=True,
    help="Path to models")

parser.add_argument("-p",
    "--pretrained_path",
    dest="pretrained_path",
    required=True,
    help="Path to pretrained embedding model")

parser.add_argument("-n",
    "--dataset_name",
    dest="dataset_name",
    choices=['bbc','yahoo','20newsgroups', 'reuters', 'ohsumed'],
    required=True,
    help="Name of dataset")

parser.add_argument("-r",
    "--restore",
    dest="restore",
    required=False,
    action='store_true',
    help="Path to models")

parser.add_argument("-l",
    "--logging",
    dest="logging",
    required=False,
    help="Path to logging file")

_StoreAction(option_strings=['-l', '--logging'], dest='logging', nargs=None, const=None, default=None, type=None, choices=None, help='Path to logging file', metavar=None)

In [3]:
# args = parser.parse_args("-d datasets/Reuters21578-Apte-90Cat/ -m models/ -p glove/glove.6B.100d.txt -n reuters".split())
args = parser.parse_args("-d datasets/ohsumed-first-20000-docs/ -m models/ -p glove/glove.6B.100d.txt -n ohsumed".split())

In [4]:
import os 

path = os.path.join(os.getcwd(), args.dataset_path)
classes = []

logging.basicConfig(
format='%(asctime)s : %(levelname)s : %(message)s',
level=logging.INFO)

logging.info(args.dataset_path)

num_categories = 0
load_dataset = None
validator = None

if args.dataset_name in ["bbc", "20newsgroups"]:
    for file in sorted(os.listdir(path)):
        if os.path.isdir(os.path.join(path, file)):
            classes.append(file)
elif args.dataset_name in ["reuters", "ohsumed"]:
    directory = os.listdir(path)[0]
    path_to_classes = os.path.join(path, directory)
    for file in sorted(os.listdir(path_to_classes)):
        if os.path.isdir(os.path.join(path_to_classes, file)):
            classes.append(file)

print(len(classes))
            
if args.dataset_name == "bbc":
    load_dataset = load_bbc_dataset
    num_categories = 5
elif args.dataset_name == "yahoo":
    load_dataset = load_yahoo_answers_dataset
    num_categories = 10
elif args.dataset_name == "20newsgroups":
    load_dataset = load_news_groups_dataset
    num_categories = 20
elif args.dataset_name == "reuters":
    load_dataset = load_reuters_dataset
    num_categories = 91
elif args.dataset_name == "ohsumed":
    load_dataset = load_ohsumed_dataset
    num_categories = 23

2020-03-03 15:12:02,612 : INFO : datasets/ohsumed-first-20000-docs/


23


In [5]:
x_train, x_test, y_train, y_test = load_dataset(args.dataset_path)

han = HANModel(
    text = x_train['text'],
    labels = y_train['target'],
    num_categories = num_categories,
    pretrained_embedded_vector_path = args.pretrained_path,
    max_features = 200000,
    max_senten_len = 100,
    max_senten_num = 30,
    embedding_size = 100,
    validation_split=0.2,
    verbose=1,
    batch_size=8,
    epochs=40)

doc2vecdm = Doc2VecDMModel(
    negative=10,
    vector_size=100,
    window=5,
    workers=cores,
    min_count=1)

doc2veccbow = Doc2VecDBOWModel(
    negative=10,
    vector_size=100,
    window=5,
    workers=cores,
    min_count=1)

sif = SIFModel(
    text = x_train['text'],
    labels = y_train['target'],
    pretrained_embedded_vector_path = args.pretrained_path,
    embedding_size=100)

lda = LDAModel(
    n_components=100,
    max_features=None,
    max_df=0.95,
    min_df=0,
    epochs=10,
    cores=cores)

lsa = LSAModel(
    svd_features=100,
    n_features=None,
    n_iter=10,
    max_df=0.95,
    min_df=0)

tfidf = TfIdfModel(
    n_features=None,
    max_df=0.95,
    min_df=0)

cbow = CBOWModel(
    max_features=None,
    max_df=0.95,
    min_df=0)
benchmark_models = [cbow, tfidf, lsa, lda, sif, doc2vecdm, doc2veccbow]

if args.dataset_name in ["bbc", "20newsgroups"]:
    train_x, test_x, train_y, test_y = train_test_split(
        x_train['text'], 
        y_train['target'], 
        test_size=0.2, 
        shuffle=True)
    train_x = train_x.reset_index(drop=True)
    train_y = train_y.reset_index(drop=True)
    test_x = test_x.reset_index(drop=True)
    test_y = test_y.reset_index(drop=True)
elif args.dataset_name in ["reuters", "ohsumed"]:
    train_x, test_x, train_y, test_y = x_train['text'], x_test['text'], y_train['target'], y_test['target']   

for model in benchmark_models:
    model.build_model()
    # .values is necessary, https://github.com/dmlc/xgboost/issues/2334
    # eli5 has specific way of hanlding input data
    # by transforming it into numpy matrix we asure that features names will be correct
    model.fit(train_x.values, train_y.values)
    pred = model.predict(test_x.values, test_y.values)
    wrong_predictions = test_y.iloc[pred != test_y.values]
    print("Model: " + model.__class__.__name__)
    print("Wrong predictions: " + str(wrong_predictions.index))
    print("Ground truth: " + str(test_y[wrong_predictions.index].to_numpy()))
    print("Predictions: " + str(pred[wrong_predictions.index]))

2020-03-03 15:15:07,950 : INFO : Training classifier CBOWModel
/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_split.py:2053: FutureWarning: You should specify a value for 'cv' instead of relying on the default value. The default value will change from 3 to 5 in version 0.22.
  warnings.warn(CV_WARNING, FutureWarning)
2020-03-03 15:19:01,443 : INFO : Predict on classifier CBOWModel
2020-03-03 15:22:19,044 : INFO : Training classifier TfIdfModel


Model: CBOWModel
Wrong predictions: Int64Index([    0,     1,     2,     8,     9,    11,    13,    14,    15,
               17,
            ...
            12718, 12720, 12721, 12722, 12724, 12726, 12728, 12729, 12730,
            12731],
           dtype='int64', length=7478)
Ground truth: [ 1 22 15 ...  5 20 22]
Predictions: [19  5 12 ... 19 13  5]


/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_split.py:2053: FutureWarning: You should specify a value for 'cv' instead of relying on the default value. The default value will change from 3 to 5 in version 0.22.
  warnings.warn(CV_WARNING, FutureWarning)
2020-03-03 15:26:53,193 : INFO : Predict on classifier TfIdfModel
2020-03-03 15:30:13,684 : INFO : Training classifier LSAModel


Model: TfIdfModel
Wrong predictions: Int64Index([    0,     1,     2,     4,     8,     9,    11,    13,    14,
               15,
            ...
            12717, 12718, 12720, 12721, 12722, 12724, 12726, 12728, 12729,
            12731],
           dtype='int64', length=7079)
Ground truth: [ 1 22 15 ...  9  5 22]
Predictions: [19  5 12 ... 11 19  5]


/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_split.py:2053: FutureWarning: You should specify a value for 'cv' instead of relying on the default value. The default value will change from 3 to 5 in version 0.22.
  warnings.warn(CV_WARNING, FutureWarning)
2020-03-03 15:31:20,679 : INFO : Predict on classifier LSAModel
2020-03-03 15:32:12,794 : INFO : Training classifier LDAModel


...

2020-03-03 15:53:25,310 : INFO : collecting all words and their counts
2020-03-03 15:53:25,311 : INFO : PROGRESS: at example #0, processed 0 words (0/s), 0 word types, 0 tags
2020-03-03 15:53:25,676 : INFO : PROGRESS: at example #10000, processed 1632857 words (4483675/s), 28098 word types, 23 tags
2020-03-03 15:53:25,693 : INFO : collected 28356 word types and 23 unique tags from a corpus of 10433 examples and 1705226 words
2020-03-03 15:53:25,694 : INFO : Loading a fresh vocabulary
2020-03-03 15:53:25,777 : INFO : effective_min_count=1 retains 28356 unique words (100% of original 28356, drops 0)
2020-03-03 15:53:25,778 : INFO : effective_min_count=1 leaves 1705226 word corpus (100% of original 1705226, drops 0)
2020-03-03 15:53:25,875 : INFO : deleting the raw counts dictionary of 28356 items
2020-03-03 15:53:25,877 : INFO : sample=0.001 downsamples 30 most-common words
2020-03-03 15:53:25,878 : INFO : downsampling leaves estimated 1346927 word corpus (79.0% of prior 1705226)
2020-03

2020-03-03 15:53:50,868 : INFO : EPOCH 12 - PROGRESS: at 47.67% examples, 637447 words/s, in_qsize 5, out_qsize 0
2020-03-03 15:53:51,869 : INFO : EPOCH 12 - PROGRESS: at 95.40% examples, 641987 words/s, in_qsize 5, out_qsize 0
2020-03-03 15:53:51,956 : INFO : worker thread finished; awaiting finish of 2 more threads
2020-03-03 15:53:51,957 : INFO : worker thread finished; awaiting finish of 1 more threads
2020-03-03 15:53:51,987 : INFO : worker thread finished; awaiting finish of 0 more threads
2020-03-03 15:53:51,988 : INFO : EPOCH - 12 : training on 1705226 raw words (1357653 effective words) took 2.1s, 636149 effective words/s
2020-03-03 15:53:53,001 : INFO : EPOCH 13 - PROGRESS: at 47.07% examples, 634357 words/s, in_qsize 5, out_qsize 0
2020-03-03 15:53:54,011 : INFO : EPOCH 13 - PROGRESS: at 95.41% examples, 641285 words/s, in_qsize 5, out_qsize 0
2020-03-03 15:53:54,099 : INFO : worker thread finished; awaiting finish of 2 more threads
2020-03-03 15:53:54,101 : INFO : worker th

2020-03-03 15:54:18,508 : INFO : EPOCH 25 - PROGRESS: at 47.67% examples, 646238 words/s, in_qsize 5, out_qsize 0
2020-03-03 15:54:19,532 : INFO : EPOCH 25 - PROGRESS: at 96.53% examples, 646602 words/s, in_qsize 5, out_qsize 0
2020-03-03 15:54:19,587 : INFO : worker thread finished; awaiting finish of 2 more threads
2020-03-03 15:54:19,593 : INFO : worker thread finished; awaiting finish of 1 more threads
2020-03-03 15:54:19,622 : INFO : worker thread finished; awaiting finish of 0 more threads
2020-03-03 15:54:19,623 : INFO : EPOCH - 25 : training on 1705226 raw words (1357570 effective words) took 2.1s, 641388 effective words/s
2020-03-03 15:54:20,641 : INFO : EPOCH 26 - PROGRESS: at 47.68% examples, 638003 words/s, in_qsize 5, out_qsize 0
2020-03-03 15:54:21,647 : INFO : EPOCH 26 - PROGRESS: at 96.53% examples, 648402 words/s, in_qsize 5, out_qsize 0
2020-03-03 15:54:21,706 : INFO : worker thread finished; awaiting finish of 2 more threads
2020-03-03 15:54:21,722 : INFO : worker th

2020-03-03 15:54:46,246 : INFO : EPOCH 38 - PROGRESS: at 47.03% examples, 630690 words/s, in_qsize 5, out_qsize 0
2020-03-03 15:54:47,261 : INFO : EPOCH 38 - PROGRESS: at 95.93% examples, 641754 words/s, in_qsize 5, out_qsize 0
2020-03-03 15:54:47,328 : INFO : worker thread finished; awaiting finish of 2 more threads
2020-03-03 15:54:47,348 : INFO : worker thread finished; awaiting finish of 1 more threads
2020-03-03 15:54:47,351 : INFO : worker thread finished; awaiting finish of 0 more threads
2020-03-03 15:54:47,352 : INFO : EPOCH - 38 : training on 1705226 raw words (1357148 effective words) took 2.1s, 640362 effective words/s
2020-03-03 15:54:48,359 : INFO : EPOCH 39 - PROGRESS: at 47.07% examples, 637921 words/s, in_qsize 5, out_qsize 0
2020-03-03 15:54:49,366 : INFO : EPOCH 39 - PROGRESS: at 95.41% examples, 644188 words/s, in_qsize 5, out_qsize 0
2020-03-03 15:54:49,457 : INFO : worker thread finished; awaiting finish of 2 more threads
2020-03-03 15:54:49,467 : INFO : worker th

Model: Doc2VecDBOWModel
Wrong predictions: Int64Index([    0,     1,     2,     4,     8,     9,    11,    12,    14,
               17,
            ...
            12717, 12719, 12720, 12721, 12724, 12725, 12726, 12728, 12730,
            12731],
           dtype='int64', length=7751)
Ground truth: [ 1 22 15 ...  9 20 22]
Predictions: [19  5 12 ... 11 13  5]


In [6]:
han.build_model()
# .values is necessary, https://github.com/dmlc/xgboost/issues/2334
# eli5 has specific way of hanlding input data
# by transforming it into numpy matrix we asure that features names will be correct
han.fit(train_x.values, train_y.values)
pred = han.predict(test_x.values, test_y.values)
wrong_predictions = test_y.iloc[pred != test_y.values]
print("Model: " + han.__class__.__name__)
print("Wrong predictions: " + str(wrong_predictions.index))
print("Ground truth: " + str(test_y[wrong_predictions.index].to_numpy()))
print("Predictions: " + str(pred[wrong_predictions.index]))

benchmark_models.append(han)

2020-03-03 16:01:18,301 : INFO : Training classifier HANModel
2020-03-03 16:01:41,051 : INFO : Total 30613 unique tokens.
2020-03-03 16:01:41,107 : INFO : Shape of data tensor: %s(10433, 30, 100)
2020-03-03 16:01:41,108 : INFO : Shape of labels tensor: %s(10433, 23)
2020-03-03 16:01:41,228 : INFO : Number of positive and negative reviews in traing and validation set
2020-03-03 16:01:41,229 : INFO : [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22]
2020-03-03 16:01:41,235 : INFO : [338, 127, 48, 936, 225, 464, 78, 380, 103, 495, 134, 382, 237, 1000, 165, 166, 238, 317, 152, 390, 441, 74, 1457]
2020-03-03 16:01:41,237 : INFO : [85, 31, 17, 227, 58, 124, 22, 93, 22, 126, 28, 109, 44, 249, 50, 34, 57, 71, 39, 135, 105, 18, 342]
2020-03-03 16:01:42,540 : INFO : Total absent words are 9133 which is 29.83% of total words


Instructions for updating:
Colocations handled automatically by placer.


2020-03-03 16:01:42,661 : WARNING : From /usr/local/lib/python3.6/dist-packages/tensorflow/python/framework/op_def_library.py:263: colocate_with (from tensorflow.python.framework.ops) is deprecated and will be removed in a future version.
Instructions for updating:
Colocations handled automatically by placer.


Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.


2020-03-03 16:01:47,390 : WARNING : From /usr/local/lib/python3.6/dist-packages/keras/backend/tensorflow_backend.py:3135: calling dropout (from tensorflow.python.ops.nn_ops) with keep_prob is deprecated and will be removed in a future version.
Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         (None, 100)               0         
_________________________________________________________________
embedding_input (Embedding)  (None, 100, 100)          20000000  
_________________________________________________________________
bidirectional_1 (Bidirection (None, 100, 100)          45300     
_________________________________________________________________
time_distributed_1 (TimeDist (None, 100, 100)          10100     
_________________________________________________________________
attention_with_context_1 (At (None, 100)               10200     
Total params: 20,065,600
Trainable params: 65,600
Non-trainable params: 20,000,000
_________________________________________________________________
_________________________________________________________________
Layer (type)                 Output Shape              Para

2020-03-03 16:01:49,669 : WARNING : From /usr/local/lib/python3.6/dist-packages/tensorflow/python/ops/math_ops.py:3066: to_int32 (from tensorflow.python.ops.math_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use tf.cast instead.


Train on 8347 samples, validate on 2086 samples
Epoch 1/40
8347/8347 [==============================] - 598s 72ms/step - loss: 2.4423 - acc: 0.2861 - val_loss: 2.2241 - val_acc: 0.3389
Epoch 2/40
8347/8347 [==============================] - 595s 71ms/step - loss: 2.1485 - acc: 0.3538 - val_loss: 2.1083 - val_acc: 0.3773
Epoch 3/40
8347/8347 [==============================] - 592s 71ms/step - loss: 2.0158 - acc: 0.3900 - val_loss: 2.0636 - val_acc: 0.3710
Epoch 4/40
8347/8347 [==============================] - 596s 71ms/step - loss: 1.9318 - acc: 0.4144 - val_loss: 2.0114 - val_acc: 0.3749
Epoch 5/40
8347/8347 [==============================] - 593s 71ms/step - loss: 1.8597 - acc: 0.4230 - val_loss: 2.0340 - val_acc: 0.3782
Epoch 6/40
8347/8347 [==============================] - 594s 71ms/step - loss: 1.7988 - acc: 0.4378 - val_loss: 2.0523 - val_acc: 0.3763
Epoch 7/40
8347/8347 [==============================] - 596s 71ms/step - loss: 1.7497 - acc: 0.4439 - val_loss: 2.0473 - val_acc: 

2020-03-03 17:11:38,395 : INFO : Total 30613 unique tokens.
2020-03-03 17:11:38,418 : INFO : Shape of data tensor: %s(10433, 30, 100)
2020-03-03 17:11:38,420 : INFO : Shape of labels tensor: %s(0, 0)
2020-03-03 17:11:59,877 : INFO : Total absent words are 9133 which is 29.83% of total words
/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_split.py:2053: FutureWarning: You should specify a value for 'cv' instead of relying on the default value. The default value will change from 3 to 5 in version 0.22.
  warnings.warn(CV_WARNING, FutureWarning)
2020-03-03 17:16:13,515 : INFO : Predict on classifier HANModel
2020-03-03 17:16:22,642 : INFO : Total 43719 unique tokens.
2020-03-03 17:16:22,658 : INFO : Shape of data tensor: %s(12733, 30, 100)
2020-03-03 17:16:22,659 : INFO : Shape of labels tensor: %s(0, 0)
2020-03-03 17:16:31,303 : INFO : Total absent words are 15798 which is 36.14% of total words


Model: HANModel
Wrong predictions: Int64Index([    0,     1,     2,     4,     5,     8,     9,    11,    12,
               13,
            ...
            12719, 12720, 12721, 12722, 12724, 12726, 12728, 12729, 12730,
            12731],
           dtype='int64', length=7379)
Ground truth: [ 1 22 15 ...  5 20 22]
Predictions: [11  5 12 ...  0  3  5]


In [7]:
import eli5
from eli5.lime import TextExplainer
from eli5.lime.samplers import MaskingTextSampler
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from preprocess import process_string

vec = CountVectorizer(
        preprocessor=process_string, # eli5 enforce use of sklearn transformation framework
        max_features=None,
        stop_words='english')

num_samples = 15000
index = 28

sampler = MaskingTextSampler(min_replace=0.5, max_replace=0.5)

In [8]:
te = TextExplainer(num_samples, vec=vec, sampler=sampler)
te.fit(train_x[index], benchmark_models[0].predict_proba)
print("Model: " + benchmark_models[0].__class__.__name__)
te.show_weights(top=20, target_names=classes)

Model: CBOWModel


In [9]:
te.show_prediction(target_names=classes)

In [10]:
te = TextExplainer(num_samples, vec=vec, sampler=sampler)
te.fit(train_x[index], benchmark_models[1].predict_proba)
print("Model: " + benchmark_models[1].__class__.__name__)
te.show_weights(top=20, target_names=classes)

Model: TfIdfModel


In [11]:
te.show_prediction(target_names=classes)

In [12]:
te = TextExplainer(num_samples, vec=vec, sampler=sampler)
te.fit(train_x[index], benchmark_models[2].predict_proba)
print("Model: " + benchmark_models[2].__class__.__name__)
te.show_weights(top=20, target_names=classes)

Model: LSAModel


In [13]:
te.show_prediction(target_names=classes)

In [14]:
te = TextExplainer(vec=vec, sampler=sampler)
te.fit(train_x[index], benchmark_models[3].predict_proba)
print("Model: " + benchmark_models[3].__class__.__name__)
te.show_weights(top=20, target_names=classes)

Model: LDAModel


In [15]:
te.show_prediction(target_names=classes)

In [17]:
index = 5

te = TextExplainer(num_samples, vec=vec, sampler=sampler)
te.fit(train_x[index], benchmark_models[0].predict_proba)
print("Model: " + benchmark_models[0].__class__.__name__)
te.show_weights(top=20, target_names=classes)

Model: CBOWModel


In [19]:
te.show_prediction(target_names=classes)

In [20]:
te = TextExplainer(num_samples, vec=vec, sampler=sampler)
te.fit(train_x[index], benchmark_models[1].predict_proba)
print("Model: " + benchmark_models[1].__class__.__name__)
te.show_weights(top=20, target_names=classes)

Model: TfIdfModel


In [21]:
te.show_prediction(target_names=classes)

In [22]:
te = TextExplainer(num_samples, vec=vec, sampler=sampler)
te.fit(train_x[index], benchmark_models[2].predict_proba)
print("Model: " + benchmark_models[2].__class__.__name__)
te.show_weights(top=20, target_names=classes)

Model: LSAModel


In [23]:
te.show_prediction(target_names=classes)

In [24]:
te = TextExplainer(num_samples, vec=vec, sampler=sampler)
te.fit(train_x[index], benchmark_models[3].predict_proba)
print("Model: " + benchmark_models[3].__class__.__name__)
te.show_weights(top=20, target_names=classes)

Model: LDAModel


In [25]:
te.show_prediction(target_names=classes)

In [26]:
te = TextExplainer(num_samples, vec=vec, sampler=sampler)
te.fit(train_x[index], benchmark_models[4].predict_proba)
print("Model: " + benchmark_models[4].__class__.__name__)
te.show_weights(top=20, target_names=classes)

AttributeError: 'tuple' object has no attribute 'copy'

In [ ]:
te.show_prediction(target_names=classes)

In [27]:
te = TextExplainer(num_samples, vec=vec, sampler=sampler)
te.fit(train_x[index], benchmark_models[5].predict_proba)
print("Model: " + benchmark_models[5].__class__.__name__)
te.show_weights(top=20, target_names=classes)

Model: Doc2VecDMModel


In [28]:
te.show_prediction(target_names=classes)

In [29]:
te = TextExplainer(num_samples, vec=vec, sampler=sampler)
te.fit(train_x[index], benchmark_models[6].predict_proba)
print("Model: " + benchmark_models[6].__class__.__name__)
te.show_weights(top=20, target_names=classes)

Model: Doc2VecDBOWModel


In [30]:
te.show_prediction(target_names=classes)

In [31]:
te = TextExplainer(num_samples, vec=vec, sampler=sampler)
te.fit(train_x[index], benchmark_models[7].predict_proba)
print("Model: " + benchmark_models[7].__class__.__name__)
te.show_weights(top=20, target_names=classes)

2020-03-03 18:06:03,100 : INFO : Total 43719 unique tokens.
2020-03-03 18:06:03,149 : INFO : Shape of data tensor: %s(15000, 30, 100)
2020-03-03 18:06:03,150 : INFO : Shape of labels tensor: %s(0, 0)
2020-03-03 18:06:39,730 : INFO : Total absent words are 15798 which is 36.14% of total words


Model: HANModel


In [32]:
te.show_prediction(target_names=classes)

In [34]:
index = 4

te = TextExplainer(num_samples, vec=vec, sampler=sampler)
te.fit(train_x[index], benchmark_models[0].predict_proba)
print("Model: " + benchmark_models[0].__class__.__name__)
te.show_weights(top=20, target_names=classes)

Model: CBOWModel


In [36]:
te.show_prediction(target_names=classes)

In [38]:
te = TextExplainer(num_samples, vec=vec, sampler=sampler)
te.fit(train_x[index], benchmark_models[1].predict_proba)
print("Model: " + benchmark_models[1].__class__.__name__)
te.show_weights(top=20, target_names=classes)

Model: TfIdfModel


In [39]:
te.show_prediction(target_names=classes)

In [40]:
te = TextExplainer(num_samples, vec=vec, sampler=sampler)
te.fit(train_x[index], benchmark_models[2].predict_proba)
print("Model: " + benchmark_models[2].__class__.__name__)
te.show_weights(top=20, target_names=classes)

Model: LSAModel


In [41]:
te.show_prediction(target_names=classes)

In [42]:
te = TextExplainer(num_samples, vec=vec, sampler=sampler)
te.fit(train_x[index], benchmark_models[3].predict_proba)
print("Model: " + benchmark_models[3].__class__.__name__)
te.show_weights(top=20, target_names=classes)

Model: LDAModel


In [43]:
te.show_prediction(target_names=classes)

In [44]:
te = TextExplainer(num_samples, vec=vec, sampler=sampler)
te.fit(train_x[index], benchmark_models[4].predict_proba)
print("Model: " + benchmark_models[4].__class__.__name__)
te.show_weights(top=20, target_names=classes)

AttributeError: 'tuple' object has no attribute 'copy'

In [ ]:
te.show_prediction(target_names=classes)

In [45]:
te = TextExplainer(num_samples, vec=vec, sampler=sampler)
te.fit(train_x[index], benchmark_models[5].predict_proba)
print("Model: " + benchmark_models[5].__class__.__name__)
te.show_weights(top=20, target_names=classes)

Model: Doc2VecDMModel


In [46]:
te.show_prediction(target_names=classes)

In [47]:
te = TextExplainer(num_samples, vec=vec, sampler=sampler)
te.fit(train_x[index], benchmark_models[6].predict_proba)
print("Model: " + benchmark_models[6].__class__.__name__)
te.show_weights(top=20, target_names=classes)

Model: Doc2VecDBOWModel


In [48]:
te.show_prediction(target_names=classes)

In [49]:
te = TextExplainer(num_samples, vec=vec, sampler=sampler)
te.fit(train_x[index], benchmark_models[7].predict_proba)
print("Model: " + benchmark_models[7].__class__.__name__)
te.show_weights(top=20, target_names=classes)

2020-03-03 18:40:41,721 : INFO : Total 43719 unique tokens.
2020-03-03 18:40:41,992 : INFO : Shape of data tensor: %s(15000, 30, 100)
2020-03-03 18:40:41,992 : INFO : Shape of labels tensor: %s(0, 0)
2020-03-03 18:42:38,019 : INFO : Total absent words are 15798 which is 36.14% of total words


Model: HANModel


In [50]:
te.show_prediction(target_names=classes)